In [20]:
import torch
import os
from torch import nn
from tqdm.auto import tqdm
from torchvision import transforms
from torchvision.datasets import ImageFolder
from torchvision.utils import make_grid
from torch.nn.utils import clip_grad_norm_
from torch.utils.data import DataLoader
import matplotlib.pyplot as plt
from wgan_gp import *
from utils import *
import opacus

# Parameters

*   image_shape: the number of pixels in each image. We further downsize every image to 64 x 64 to be compatible with the self-attention GAN architecture
*   n_classes: the number of classes (10, since there are 10 different emojis)
*   image_path: path to image folder
*   n_epochs: the number of times to iterate through the entire dataset when training
*   z_dim: the dimension of the noise vector
*   display_step: how often to display/visualize the images
*   batch_size: the number of images per forward/backward pass
*   lr: the learning rate
*   beta_1, beta_2: coefficients used for computing running averages of gradient and its square (used for Adam optimizer)
*   lambda_gp: weight of the gradient penalty
*   device: the device type
*   g_conv_dim: the number of dimensions in the last convolutional layer of the generator
*   d_conv_dim: the number of dimensions in the first convolutional layer of the discriminator
*   ckpt_epoch: how often to save model checkpoint

In [12]:
image_shape = (3, 64, 64)
n_classes = 10
image_path = 'generated/csawgan_gp'
n_epochs = 100
z_dim = 64
display_step = 500
batch_size = 128
lr = 0.0002
beta_1 = 0.5
beta_2 = 0.999
lambda_gp = 10
g_conv_dim = 64
d_conv_dim = 64
ckpt_epoch = 2
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [13]:
transform = transforms.Compose([
    transforms.Resize((image_shape[1], image_shape[2])),
    transforms.ToTensor(),
    transforms.Normalize((0.5,), (0.5,)),
])

dataset = ImageFolder(image_path, transform=transform)

dataloader = DataLoader(
    dataset,
    batch_size=batch_size,
    shuffle=True)

# Initialize generator, discriminator, optimizers

In [18]:
generator_input_dim, discriminator_im_chan = get_input_dimensions(z_dim, image_shape, n_classes)

gen = Generator(image_shape[1], generator_input_dim, g_conv_dim).to(device)
gen_opt = torch.optim.Adam(gen.parameters(), lr=lr, betas=(beta_1, beta_2))
disc = Discriminator(discriminator_im_chan, d_conv_dim).to(device)
disc_opt = torch.optim.Adam(disc.parameters(), lr=lr, betas=(beta_1, beta_2))

gen = gen.apply(weights_init)
disc = disc.apply(weights_init)

In [19]:
print(disc)

Discriminator(
  (l1): Sequential(
    (0): SpectralNorm(
      (module): Conv2d(13, 64, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1))
    )
    (1): LeakyReLU(negative_slope=0.2)
  )
  (l2): Sequential(
    (0): SpectralNorm(
      (module): Conv2d(64, 128, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1))
    )
    (1): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): LeakyReLU(negative_slope=0.2)
  )
  (l3): Sequential(
    (0): SpectralNorm(
      (module): Conv2d(128, 256, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1))
    )
    (1): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): LeakyReLU(negative_slope=0.2)
  )
  (l4): Sequential(
    (0): SpectralNorm(
      (module): Conv2d(256, 512, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1))
    )
    (1): BatchNorm2d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): LeakyReLU(negative_slope=0.2)
  )
  (last): Sequ

# Training

In [47]:
def train(start_epoch, n_epochs, dataloader, gen, gen_opt, disc, disc_opt, save_path):
    cur_step = 0
    generator_losses = []
    discriminator_losses = []

    noise_and_labels = False
    fake = False

    fake_image_and_labels = False
    real_image_and_labels = False
    disc_fake_pred = False
    disc_real_pred = False

    for epoch in range(start_epoch, start_epoch + n_epochs):
        # Dataloader returns the batches and the labels
        for real, labels in tqdm(dataloader):
            print(cur_step)
            for param in disc.parameters(): 
                param.accumulated_grads = []
            cur_batch_size = len(real)
            # Flatten the batch of real images from the dataset
            real = real.to(device)

            one_hot_labels = get_one_hot_labels(labels.to(device), n_classes)
            image_one_hot_labels = one_hot_labels[:, :, None, None]
            image_one_hot_labels = image_one_hot_labels.repeat(1, 1, image_shape[1], image_shape[2])

            # Zero out the discriminator gradients
            disc_opt.zero_grad()
            # Get noise corresponding to the current batch_size 
            fake_noise = get_noise(cur_batch_size, z_dim, device=device)

            noise_and_labels = combine_vectors(fake_noise, one_hot_labels)
            
            for i in range(cur_batch_size): 
                fake = gen(torch.unsqueeze(noise_and_labels[i], 0))

                fake_image_and_labels = combine_vectors(fake.detach(), torch.unsqueeze(image_one_hot_labels[i], 0))
                real_image_and_labels = combine_vectors(torch.unsqueeze(real[i], 0), torch.unsqueeze(image_one_hot_labels[i], 0))
                disc_fake_pred = disc(fake_image_and_labels)
                disc_real_pred = disc(real_image_and_labels)

                gp = compute_gradient_penalty(disc, torch.unsqueeze(real[i], 0), fake.detach(), torch.unsqueeze(image_one_hot_labels[i], 0), device=device)
                disc_loss = torch.mean(disc_fake_pred) - torch.mean(disc_real_pred) + gp * lambda_gp

                disc_loss.backward(retain_graph=True)
                # disc_opt.step() 

                # Keep track of the average discriminator loss
                discriminator_losses += [disc_loss.item()]

                ### Update generator ###
#                 # Zero out the generator gradients
#                 gen_opt.zero_grad()

                fake_image_and_labels = combine_vectors(fake, torch.unsqueeze(image_one_hot_labels[i], 0))
                disc_fake_pred = disc(fake_image_and_labels)
                gen_loss = -torch.mean(disc_fake_pred)
                gen_loss.backward()
                gen_opt.step()
            
                for param in disc.parameters(): 
                    print(param)
                    print(param.grad)
                    if param.grad is None: 
                        continue
                    per_sample_grad = param.grad.detach().clone()
                    clip_grad_norm_(per_sample_grad, max_norm=1)
                    param.accumulated_grads.append(per_sample_grad)

                # Keep track of the generator losses
                generator_losses += [gen_loss.item()]
            
            # Aggregate back
            for param in disc.parameters(): 
                param.grad = torch.stack(param.accumulated_grads, dim=0)
                
            for param in disc.parameters(): 
                param = param - lr * param.grad
                param += torch.normal(mean=0, std=1.5)
                param.grad = 0

            if cur_step % display_step == 0 and cur_step > 0:
                gen_mean = sum(generator_losses[-display_step:]) / display_step
                disc_mean = sum(discriminator_losses[-display_step:]) / display_step
                print(f"Step {cur_step}: Generator loss: {gen_mean}, discriminator loss: {disc_mean}")
                show_tensor_images(fake)
                show_tensor_images(real)
                step_bins = 20
                x_axis = sorted([i * step_bins for i in range(len(generator_losses) // step_bins)] * step_bins)
                num_examples = (len(generator_losses) // step_bins) * step_bins
                plt.plot(
                    range(num_examples // step_bins), 
                    torch.Tensor(generator_losses[:num_examples]).view(-1, step_bins).mean(1),
                    label="Generator Loss"
                )
                plt.plot(
                    range(num_examples // step_bins), 
                    torch.Tensor(discriminator_losses[:num_examples]).view(-1, step_bins).mean(1),
                    label="Discriminator Loss"
                )
                plt.legend()
                plt.show()
            elif cur_step == 0:
                print("Start training...")
            cur_step += 1
            
        if epoch % ckpt_epoch == 0:
            ckpt_dict = {
                'epoch': epoch,
                'gen_state_dict': gen.state_dict(),
                'gen_opt': gen_opt.state_dict(),
                'disc_state_dict': disc.state_dict(),
                'disc_opt': disc_opt.state_dict(),
            }
            checkpoint_path = os.path.join(save_path, f'epoch_{epoch}.pth.tar')
            torch.save(ckpt_dict, checkpoint_path)

In [48]:
train(0, n_epochs, dataloader, gen, gen_opt, disc, disc_opt, 'model_ckpt/cSAWGAN-GP-DP')

  0%|          | 0/52 [00:00<?, ?it/s]

0
Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-2.0022e+00, -3.9654e-01, -6.1716e-01, -5.1999e-01,  3.1981e+00,
        -2.2701e+00, -1.9017e+00, -1.7336e-01, -1.9623e-01, -2.0170e-01,
         2.1500e+00, -9.3310e-02,  4.6199e-01,  1.5469e-01, -9.7702e-02,
         3.2199e-02, -3.2110e-02, -1.0994e+00, -4.6526e-03, -3.5807e-02,
         7.1667e

Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-3.6980, -0.0419, -1.1190, -0.6686,  4.5780, -3.5377, -3.6029, -0.4951,
        -0.4857, -0.4163,  4.1685, -0.2827,  1.3226,  2.0106,  1.9397, -0.0484,
         0.2368, -1.7990, -0.1335, -0.2298,  1.2040, -0.3955, -5.3568, -0.3308,
        -1.0856, -0.8148, -1.0609, -1.4567,  1.4317,  4.7497,  1.6416,

Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-5.6349,  0.3354, -1.6588, -0.7212,  6.8671, -4.8015, -5.4811, -0.9162,
        -0.8253, -0.6849,  6.7161, -0.4903,  2.0053,  3.3688,  2.4124, -0.1180,
         0.5512, -3.0489,  0.6001, -0.4225,  2.1087, -0.2423, -4.6173, -0.6658,
        -1.4908, -1.3146, -1.5775, -1.9284,  3.2844,  7.0225,  2.6240,

Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-7.5280e+00,  3.1188e-01, -2.1262e+00, -1.0728e+00,  8.1743e+00,
        -5.9031e+00, -6.5848e+00, -1.2725e+00, -1.1386e+00, -8.8735e-01,
         8.5704e+00, -7.3480e-01,  2.8592e+00,  4.5801e+00, -1.0970e+00,
        -1.2520e-01,  3.5965e-01, -4.3800e+00,  4.0833e-01, -6.8302e-01,
         2.7918e+0

...

Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-7.3476e+01, -7.5390e+00, -1.7517e+01, -1.4620e+01,  8.1923e+01,
        -6.0271e+01, -5.2130e+01, -9.0771e+00, -7.9047e+00, -5.6523e+00,
         6.9391e+01, -4.4740e+00,  1.6753e+01,  4.0677e+01, -1.2401e-01,
         3.3318e-01, -1.4330e+00, -4.5095e+01, -1.2814e+01, -5.1951e+00,
         1.7172e+0

Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-77.0912,  -9.2729, -17.9112, -15.4401,  85.5702, -62.9566, -53.7813,
         -9.4304,  -8.0862,  -5.6092,  70.9650,  -4.5368,  15.3558,  41.6819,
          5.4157,   0.4876,  -3.8019, -49.1503, -15.5852,  -5.5283,  17.3822,
        -24.8935, -18.7910,  -5.6211, -29.1512,  10.2074, -19.1903, -39.6408

Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-79.9887, -10.0957, -18.6376, -16.0277,  87.6102, -65.8721, -56.6724,
         -9.5580,  -8.1765,  -5.8783,  73.2176,  -4.4242,  15.6602,  44.0105,
         13.2082,   0.4331,  -2.9224, -49.6712, -15.8836,  -5.4288,  17.3446,
        -25.2165, -21.7167,  -5.6797, -30.3537,   9.8636, -19.9036, -40.0709

Parameter containing:
tensor([ 0.0684,  0.1323, -0.1642,  0.0823,  0.0509,  0.1732,  0.0478, -0.0551,
        -0.2007, -0.2059,  0.1489, -0.1646,  0.2332,  0.1242, -0.0247, -0.1376,
         0.0991, -0.0083,  0.0399, -0.1348,  0.0592,  0.0450, -0.0045, -0.1987,
         0.1918, -0.0792, -0.0139,  0.1729, -0.0468,  0.0981,  0.1689,  0.1505,
        -0.0457,  0.1631,  0.0436,  0.0410, -0.2197,  0.1022,  0.1263,  0.1583,
         0.0615,  0.0542,  0.0362,  0.0455,  0.0895, -0.1509, -0.2119,  0.1106,
        -0.0671,  0.1453, -0.1137, -0.0928,  0.2271,  0.2809,  0.1725, -0.0909,
         0.1248,  0.2105,  0.1663, -0.0871,  0.1872, -0.2238,  0.1055,  0.2279],
       requires_grad=True)
tensor([-82.3007,  -9.9444, -19.1543, -16.3029,  92.3792, -67.4176, -58.4210,
         -9.9104,  -8.5220,  -6.0517,  75.3847,  -4.6340,  16.0610,  44.0425,
         12.9506,   0.3759,  -3.2036, -51.1966, -16.5422,  -5.6757,  18.3025,
        -25.2601, -24.3248,  -5.9271, -30.8628,   9.3133, -20.4846, -41.0196

KeyboardInterrupt: 